First, check we are in the main project directory:

In [1]:
from os import getcwd
print(getcwd())

/Users/u1874623/Documents/GitHub/covid-19-in-households-public/tutorials


If we are instead in the `tutorials` subdirectory, move up to it by uncommenting this line:

In [2]:
cd ..

/Users/u1874623/Documents/GitHub/covid-19-in-households-public


Import functions etc:

In [4]:
from argparse import ArgumentParser
from os import mkdir
from os.path import isdir, isfile
from pickle import load, dump
from copy import copy, deepcopy
from multiprocessing import Pool
from numpy import append, arange, array, exp, log, ones, sum, vstack, where, zeros
from numpy.linalg import eig
from numpy.random import rand
from pandas import read_csv
from time import time as get_time
from scipy.integrate import solve_ivp, trapezoid
from matplotlib.pyplot import subplots
from matplotlib.cm import get_cmap
from model.preprocessing import (add_vuln_class, add_vulnerable_hh_members,
estimate_beta_ext, HouseholdPopulation, make_initial_condition_by_eigenvector,
map_SEPIR_to_SEPIRQ,SEPIRInput, SEPIRQInput)
from model.common import SEPIRRateEquations, SEPIRQRateEquations
from model.imports import NoImportModel
from model.specs import (TWO_AGE_UK_SPEC, TWO_AGE_EXT_SEPIRQ_SPEC,
TWO_AGE_SEPIR_SPEC_FOR_FITTING)

Constants and functions we need to run the analysis:

In [5]:
if isdir('outputs/oohi') is False:
    mkdir('outputs/oohi')

DOUBLING_TIME = 10
growth_rate = log(2) / DOUBLING_TIME

SEPIR_SPEC = {**TWO_AGE_SEPIR_SPEC_FOR_FITTING, **TWO_AGE_UK_SPEC}
OOHI_SPEC = {**TWO_AGE_UK_SPEC, **TWO_AGE_EXT_SEPIRQ_SPEC}

relative_iso_rates = [1.0, 1.0, 0.5]

vuln_ext_scale = 0


# List of observed household compositions
composition_list = read_csv(
    'inputs/eng_and_wales_adult_child_vuln_composition_list.csv',
    header=0).to_numpy()
# Proportion of households which are in each composition
comp_dist = read_csv(
    'inputs/eng_and_wales_adult_child_vuln_composition_dist.csv',
    header=0).to_numpy().squeeze()

if isfile('outputs/oohi/beta_ext.pkl') is True:
    with open('outputs/oohi/beta_ext.pkl', 'rb') as f:
        beta_ext = load(f)
else:
    # List of observed household compositions
    fitting_comp_list = read_csv(
        'inputs/eng_and_wales_adult_child_composition_list.csv',
        header=0).to_numpy()
    # Proportion of households which are in each composition
    fitting_comp_dist = read_csv(
        'inputs/eng_and_wales_adult_child_composition_dist.csv',
        header=0).to_numpy().squeeze()
    model_input_to_fit = SEPIRInput(SEPIR_SPEC,
                                    fitting_comp_list,
                                    fitting_comp_dist)
    household_population_to_fit = HouseholdPopulation(
        fitting_comp_list, fitting_comp_dist, model_input_to_fit)
    print('number of states for 2-class pop is',
            household_population_to_fit.Q_int.shape)
    rhs_to_fit = SEPIRRateEquations(model_input_to_fit,
                                    household_population_to_fit,
                                    NoImportModel(5,2))
    beta_ext = estimate_beta_ext(household_population_to_fit,
                                 rhs_to_fit,
                                 growth_rate)
    with open('outputs/oohi/beta_ext.pkl', 'wb') as f:
        dump(beta_ext, f)

vuln_prop = 2.2/56
adult_class = 1

import_model = NoImportModel(6,3)

prev=1.0e-3 # Starting prevalence
starting_immunity=1e-2 # Starting antibody prev/immunity

Set up the analysis:

In [6]:
pre_npi_input =  SEPIRInput(SEPIR_SPEC,
                                 composition_list,
                                 comp_dist)
pre_npi_input.k_ext *= beta_ext
pre_npi_input = add_vuln_class(pre_npi_input,
                    vuln_prop,
                    adult_class,
                    vuln_ext_scale)
pre_npi_household_population = HouseholdPopulation(
    composition_list, comp_dist, pre_npi_input)
pre_npi_rhs = SEPIRRateEquations(
    pre_npi_input,
    pre_npi_household_population,
    import_model)
H0_pre_npi = make_initial_condition_by_eigenvector(
                                    growth_rate,
                                    pre_npi_input,
                                    pre_npi_household_population,
                                    pre_npi_rhs,
                                    prev,
                                    starting_immunity)


if isfile('outputs/oohi/map_matrix.pkl') is True:
    with open('outputs/oohi/map_matrix.pkl', 'rb') as f:
        map_matrix = load(f)
else:
    print('calculating map matrix...')
    basic_npi_spec = deepcopy(OOHI_SPEC)
    basic_npi_input = SEPIRQInput(basic_npi_spec,
                                composition_list,
                                comp_dist)
    basic_npi_input.k_ext = beta_ext * basic_npi_input.k_ext
    basic_npi_input = add_vuln_class(basic_npi_input,
                        vuln_prop,
                        adult_class,
                        vuln_ext_scale)
    basic_npi_population = HouseholdPopulation(
        composition_list, comp_dist, basic_npi_input)
    map_mat_start = get_time()
    map_matrix = map_SEPIR_to_SEPIRQ(
                                pre_npi_household_population,
                                basic_npi_population)
    print('map matrix calculation took',
            (get_time()-map_mat_start),
            'seconds')
    map_matrix = map_matrix
    with open('outputs/oohi/map_matrix.pkl', 'wb') as f:
                dump(map_matrix, f)

/Users/u1874623/opt/anaconda3/lib/python3.8/site-packages/scipy/sparse/linalg/dsolve/linsolve.py:407: SparseEfficiencyWarning: splu requires CSC matrix format
  warn('splu requires CSC matrix format', SparseEfficiencyWarning)


Precondtioner computed in 0.12981200218200684s
multiplier calculation took 1.7993783950805664 seconds.


Do the analysis:

In [7]:
iso_rate = 1/5 # Cases identified on average within 5 days of infection
iso_prob = 0 # Turn off isolation by setting adherence probability to zero

p = [iso_rate, iso_prob]

In [8]:
start_time = get_time()

this_spec = deepcopy(OOHI_SPEC)
this_spec['exp_iso_rate'] = p[0] * relative_iso_rates[0] * ones(2,)
this_spec['pro_iso_rate'] = p[0] * relative_iso_rates[1] * ones(2,)
this_spec['inf_iso_rate'] = p[0] * relative_iso_rates[2] * ones(2,)
this_spec['ad_prob'] = p[1]
model_input = SEPIRQInput(this_spec, composition_list, comp_dist)
model_input.k_ext = beta_ext * model_input.k_ext
model_input = add_vuln_class(model_input,
                    vuln_prop,
                    adult_class,
                    vuln_ext_scale)

household_population = HouseholdPopulation(
    composition_list, comp_dist, model_input)
rhs = SEPIRQRateEquations(
    model_input,
    household_population,
    import_model)

H0_iso = H0_pre_npi * map_matrix

'''Record the starting state for future reference:'''

S0 = H0_iso.T.dot(household_population.states[:, ::6]) / \
                model_input.ave_hh_by_class
E0 = H0_iso.T.dot(household_population.states[:, 1::6]) / \
                model_input.ave_hh_by_class
P0 = H0_iso.T.dot(household_population.states[:, 2::6]) / \
                model_input.ave_hh_by_class
I0 = H0_iso.T.dot(household_population.states[:, 3::6]) / \
                model_input.ave_hh_by_class
R0 = H0_iso.T.dot(household_population.states[:, 4::6]) / \
                model_input.ave_hh_by_class
Q0 = H0_iso.T.dot(household_population.states[:, 5::6]) / \
                model_input.ave_hh_by_class


no_days = 100
tspan = (0.0, no_days)
solution = solve_ivp(rhs,
                     tspan,
                     H0_iso,
                     first_step=0.001,
                     atol=1e-16)

t = solution.t
H = solution.y

print('Calculations took', (get_time()-start_time), 'seconds.')

class_idx= [0]
range(len(class_idx))= range(0, 1)
class_idx is of type <class 'numpy.ndarray'>
i= 0
class_idx= [0]
range(len(class_idx))= range(0, 1)
class_idx is of type <class 'numpy.ndarray'>
i= 0
class_idx= [0]
range(len(class_idx))= range(0, 1)
class_idx is of type <class 'numpy.ndarray'>
i= 0
class_idx= [0]
range(len(class_idx))= range(0, 1)
class_idx is of type <class 'numpy.ndarray'>
i= 0
class_idx= [0]
range(len(class_idx))= range(0, 1)
class_idx is of type <class 'numpy.ndarray'>
i= 0
class_idx= [1]
range(len(class_idx))= range(0, 1)
class_idx is of type <class 'numpy.ndarray'>
i= 0
class_idx= [0 1]
range(len(class_idx))= range(0, 2)
class_idx is of type <class 'numpy.ndarray'>
i= 0
i= 1
class_idx= [0 1]
range(len(class_idx))= range(0, 2)
class_idx is of type <class 'numpy.ndarray'>
i= 0
i= 1
class_idx= [0 1]
range(len(class_idx))= range(0, 2)
class_idx is of type <class 'numpy.ndarray'>
i= 0
i= 1
class_idx= [0 1]
range(len(class_idx))= range(0, 2)
class_idx is of type <class

new_state= [3 0 0 0 1 0 0 1 0 0 0 0]
infection in vuln class, rate 0.0261159095394361
class_idx= [0 2]
old_state= [3 0 0 1 0 0 1 0 0 0 0 0]
new_state= [3 0 0 1 0 0 0 1 0 0 0 0]
infection in vuln class, rate 0.01305795476971805
class_idx= [0 2]
old_state= [3 0 1 0 0 0 1 0 0 0 0 0]
new_state= [3 0 1 0 0 0 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [3 1 0 0 0 0 1 0 0 0 0 0]
new_state= [3 1 0 0 0 0 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [4 0 0 0 0 0 1 0 0 0 0 0]
new_state= [4 0 0 0 0 0 0 1 0 0 0 0]
class_idx= [0 2]
range(len(class_idx))= range(0, 2)
class_idx is of type <class 'numpy.ndarray'>
i= 0
i= 1
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [0 0 0 0 0 5 1 0 0 0 0 0]
new_state= [0 0 0 0 0 5 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [0 0 0 0 1 4 1 0 0 0 0 0]
new_state= [0 0 0 0 1 4 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [0 0 0 0 2 3 

class_idx= [0 2]
old_state= [0 3 1 1 0 0 1 0 0 0 0 0]
new_state= [0 3 1 1 0 0 0 1 0 0 0 0]
infection in vuln class, rate 0.023358779609765738
class_idx= [0 2]
old_state= [0 3 2 0 0 0 1 0 0 0 0 0]
new_state= [0 3 2 0 0 0 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [0 4 0 0 0 1 1 0 0 0 0 0]
new_state= [0 4 0 0 0 1 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [0 4 0 0 1 0 1 0 0 0 0 0]
new_state= [0 4 0 0 1 0 0 1 0 0 0 0]
infection in vuln class, rate 0.023358779609765738
class_idx= [0 2]
old_state= [0 4 0 1 0 0 1 0 0 0 0 0]
new_state= [0 4 0 1 0 0 0 1 0 0 0 0]
infection in vuln class, rate 0.011679389804882869
class_idx= [0 2]
old_state= [0 4 1 0 0 0 1 0 0 0 0 0]
new_state= [0 4 1 0 0 0 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [0 5 0 0 0 0 1 0 0 0 0 0]
new_state= [0 5 0 0 0 0 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 2]
old_state= [1 0 0 0 0 4 1 0 0 0 0 0]
new_state= [1 0 0 0 

class_idx= [1 2]
range(len(class_idx))= range(0, 2)
class_idx is of type <class 'numpy.ndarray'>
i= 0
i= 1
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [0 0 0 0 0 1 1 0 0 0 0 0]
new_state= [0 0 0 0 0 1 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [0 0 0 0 1 0 1 0 0 0 0 0]
new_state= [0 0 0 0 1 0 0 1 0 0 0 0]
infection in vuln class, rate 0.06874136358820554
class_idx= [1 2]
old_state= [0 0 0 1 0 0 1 0 0 0 0 0]
new_state= [0 0 0 1 0 0 0 1 0 0 0 0]
infection in vuln class, rate 0.03437068179410277
class_idx= [1 2]
old_state= [0 0 1 0 0 0 1 0 0 0 0 0]
new_state= [0 0 1 0 0 0 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [0 1 0 0 0 0 1 0 0 0 0 0]
new_state= [0 1 0 0 0 0 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [1 0 0 0 0 0 1 0 0 0 0 0]
new_state= [1 0 0 0 0 0 0 1 0 0 0 0]
class_idx= [0 1 2]
range(len(class_idx))= range(0, 3)
class_idx is of type <class 'numpy.ndarray'>
i= 0
i= 1
i=

class_idx= [0 1 2]
range(len(class_idx))= range(0, 3)
class_idx is of type <class 'numpy.ndarray'>
i= 0
i= 1
i= 2
infection in vuln class, rate 0.0
class_idx= [0 1 2]
old_state= [0 0 0 0 0 3 0 0 0 0 0 1 1 0 0 0 0 0]
new_state= [0 0 0 0 0 3 0 0 0 0 0 1 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 1 2]
old_state= [0 0 0 0 1 2 0 0 0 0 0 1 1 0 0 0 0 0]
new_state= [0 0 0 0 1 2 0 0 0 0 0 1 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 1 2]
old_state= [0 0 0 0 2 1 0 0 0 0 0 1 1 0 0 0 0 0]
new_state= [0 0 0 0 2 1 0 0 0 0 0 1 0 1 0 0 0 0]
infection in vuln class, rate 0.0
class_idx= [0 1 2]
old_state= [0 0 0 0 3 0 0 0 0 0 0 1 1 0 0 0 0 0]
new_state= [0 0 0 0 3 0 0 0 0 0 0 1 0 1 0 0 0 0]
infection in vuln class, rate 0.0522318190788722
class_idx= [0 1 2]
old_state= [0 0 0 1 0 2 0 0 0 0 0 1 1 0 0 0 0 0]
new_state= [0 0 0 1 0 2 0 0 0 0 0 1 0 1 0 0 0 0]
infection in vuln class, rate 0.03693347346437942
class_idx= [0 1 2]
old_state= [0 0 0 1 1 1 0 0 0 0 0 1 1 0 0 0 0 0

...

class_idx= [1 2]
range(len(class_idx))= range(0, 2)
class_idx is of type <class 'numpy.ndarray'>
i= 0
i= 1
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [0 0 0 0 0 1 1 0 0 0 0 4]
new_state= [0 0 0 0 0 1 0 1 0 0 0 4]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [0 0 0 0 1 0 1 0 0 0 0 4]
new_state= [0 0 0 0 1 0 0 1 0 0 0 4]
infection in vuln class, rate 0.06874136358820554
class_idx= [1 2]
old_state= [0 0 0 1 0 0 1 0 0 0 0 4]
new_state= [0 0 0 1 0 0 0 1 0 0 0 4]
infection in vuln class, rate 0.03437068179410277
class_idx= [1 2]
old_state= [0 0 1 0 0 0 1 0 0 0 0 4]
new_state= [0 0 1 0 0 0 0 1 0 0 0 4]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [0 1 0 0 0 0 1 0 0 0 0 4]
new_state= [0 1 0 0 0 0 0 1 0 0 0 4]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [1 0 0 0 0 0 1 0 0 0 0 4]
new_state= [1 0 0 0 0 0 0 1 0 0 0 4]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [0 0 0 0 0 1 1 0 0 0 1 3]
new_state= [0 0 0 0 0 1

new_state= [0 0 0 0 0 1 0 2 1 2 0 0]
infection in vuln class, rate 0.07685518092462823
class_idx= [1 2]
old_state= [0 0 0 0 1 0 1 1 1 2 0 0]
new_state= [0 0 0 0 1 0 0 2 1 2 0 0]
infection in vuln class, rate 0.14559654451283377
class_idx= [1 2]
old_state= [0 0 0 1 0 0 1 1 1 2 0 0]
new_state= [0 0 0 1 0 0 0 2 1 2 0 0]
infection in vuln class, rate 0.111225862718731
class_idx= [1 2]
old_state= [0 0 1 0 0 0 1 1 1 2 0 0]
new_state= [0 0 1 0 0 0 0 2 1 2 0 0]
infection in vuln class, rate 0.07685518092462823
class_idx= [1 2]
old_state= [0 1 0 0 0 0 1 1 1 2 0 0]
new_state= [0 1 0 0 0 0 0 2 1 2 0 0]
infection in vuln class, rate 0.07685518092462823
class_idx= [1 2]
old_state= [1 0 0 0 0 0 1 1 1 2 0 0]
new_state= [1 0 0 0 0 0 0 2 1 2 0 0]
infection in vuln class, rate 0.030742072369851287
class_idx= [1 2]
old_state= [0 0 0 0 0 1 1 1 2 0 0 1]
new_state= [0 0 0 0 0 1 0 2 2 0 0 1]
infection in vuln class, rate 0.030742072369851287
class_idx= [1 2]
old_state= [0 0 0 0 1 0 1 1 2 0 0 1]
new_state= [0

new_state= [0 1 0 0 0 0 1 2 0 0 1 1]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [1 0 0 0 0 0 2 1 0 0 1 1]
new_state= [1 0 0 0 0 0 1 2 0 0 1 1]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [0 0 0 0 0 1 2 1 0 0 2 0]
new_state= [0 0 0 0 0 1 1 2 0 0 2 0]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [0 0 0 0 1 0 2 1 0 0 2 0]
new_state= [0 0 0 0 1 0 1 2 0 0 2 0]
infection in vuln class, rate 0.13748272717641108
class_idx= [1 2]
old_state= [0 0 0 1 0 0 2 1 0 0 2 0]
new_state= [0 0 0 1 0 0 1 2 0 0 2 0]
infection in vuln class, rate 0.06874136358820554
class_idx= [1 2]
old_state= [0 0 1 0 0 0 2 1 0 0 2 0]
new_state= [0 0 1 0 0 0 1 2 0 0 2 0]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [0 1 0 0 0 0 2 1 0 0 2 0]
new_state= [0 1 0 0 0 0 1 2 0 0 2 0]
infection in vuln class, rate 0.0
class_idx= [1 2]
old_state= [1 0 0 0 0 0 2 1 0 0 2 0]
new_state= [1 0 0 0 0 0 1 2 0 0 2 0]
infection in vuln class, rate 0.06874136358820554
class_

class_idx= [2]
range(len(class_idx))= range(0, 1)
class_idx is of type <class 'numpy.ndarray'>
i= 0
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 0 5]
new_state= [0 1 0 0 0 5]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 1 4]
new_state= [0 1 0 0 1 4]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 2 3]
new_state= [0 1 0 0 2 3]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 3 2]
new_state= [0 1 0 0 3 2]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 4 1]
new_state= [0 1 0 0 4 1]
infection in vuln class, rate 0.0
class_idx= [2]
old_state= [1 0 0 0 5 0]
new_state= [0 1 0 0 5 0]
infection in vuln class, rate 0.028063544169039757
class_idx= [2]
old_state= [1 0 0 1 0 4]
new_state= [0 1 0 1 0 4]
infection in vuln class, rate 0.06874136358820554
class_idx= [2]
old_state= [1 0 0 1 1 3]
new_state= [0 1 0 1 1 3]
infection in vuln class, rate 0.048607484341230155
class_idx= [2]
old_state

Calculations took 55.04687809944153 seconds.


Calculate outputs:

In [9]:
S = H.T.dot(household_population.states[:, ::6])
E = H.T.dot(household_population.states[:, 1::6])
P = H.T.dot(household_population.states[:, 2::6])
I = H.T.dot(household_population.states[:, 3::6])
R = H.T.dot(household_population.states[:, 4::6])
Q = H.T.dot(household_population.states[:, 5::6])

E_vuln_present = \
    H[
        where(household_population.composition_by_state[:,2]>0)[0],
        :].T.dot(
        household_population.states[
            where(household_population.composition_by_state[:,2]>0)[0],
            1::6]
        )
I_vuln_present = \
    H[
        where(household_population.composition_by_state[:,2]>0)[0],
        :].T.dot(
        household_population.states[
            where(household_population.composition_by_state[:,2]>0)[0],
            3::6]
        )

vuln_peak = 100 * max(I[:, 2]) / \
                model_input.ave_hh_by_class[2]
vuln_end = 100 * R[-1, 2] / \
                model_input.ave_hh_by_class[2]
iso_peak = 100 * max(Q.sum(axis=1)) / model_input.ave_hh_size
Q_all = Q.sum(axis=1) / model_input.ave_hh_size
cum_iso = 100 * trapezoid(Q_all, t)

Time series of E's and I's restricted to households with at least one vulnerable member:

In [10]:
print('E(at least one vuln present)=',E_vuln_present/model_input.ave_hh_by_class)
print('I(at least one vuln present)=',I_vuln_present/model_input.ave_hh_by_class)

E(at least one vuln present)= [[9.69758130e-05 2.92503230e-05 5.63883779e-29]
 [9.69564212e-05 2.92444741e-05 2.99560508e-12]
 [9.67628741e-05 2.91861110e-05 3.62354616e-10]
 [9.51782562e-05 2.87092850e-05 2.65089028e-08]
 [9.30170411e-05 2.80620790e-05 1.33397923e-07]
 [9.00491545e-05 2.71800106e-05 4.30531796e-07]
 [8.59393377e-05 2.59740792e-05 1.18182094e-06]
 [8.08734892e-05 2.45202201e-05 2.79898901e-06]
 [7.52315892e-05 2.29630111e-05 5.86043777e-06]
 [6.95611187e-05 2.15085363e-05 1.10736538e-05]
 [6.45246453e-05 2.04074722e-05 1.91649427e-05]
 [6.08029475e-05 1.99229724e-05 3.06986204e-05]
 [5.89787697e-05 2.02841359e-05 4.57352961e-05]
 [5.93759240e-05 2.16590036e-05 6.40712192e-05]
 [6.22111275e-05 2.42356128e-05 8.55240410e-05]
 [6.77642571e-05 2.83031661e-05 1.10090887e-04]
 [7.33598293e-05 3.21674534e-05 1.28999544e-04]
 [7.81558873e-05 3.54241949e-05 1.43239100e-04]
 [8.33694188e-05 3.89367353e-05 1.57619700e-04]
 [8.93861144e-05 4.29660681e-05 1.73410542e-04]
 [9.651297

Calculation above suggests infections are present and evolve in households with vulnerable members, but no spread into this class happens.

In the boxes below, we explicitly calculate what our internal transmission matrix thinks the infections into the vulnerable class should look like:

In [ ]:
states = household_population.states
Q_int = household_population.Q_int

In [ ]:
inf_possible = where(((states[:,2::6]+states[:,3::6]).sum(1)>0)&(states[:,12]>0))[0]

In [ ]:
print((rhs.states_pro_only[inf_possible,:]+rhs.states_inf_only[inf_possible,:]).sum(1).min())

In [ ]:
inf_to = zeros(len(inf_possible),dtype=int)
for k in range(len(inf_possible)):
    old_state = copy(states[inf_possible[k], :])
    new_state = old_state.copy()
    new_state[12] -= 1
    new_state[13] += 1
    inf_to[k] = where(abs(states-new_state).sum(1)==0)[0]

In [ ]:
for i in range(1000,1010):
        print('from',states[inf_possible[i],:],'to',states[inf_to[i],:],'at rate',Q_int[inf_possible[i],inf_to[i]])

In [ ]:
inf_rates = Q_int[inf_possible,inf_to]

In [ ]:
print(inf_rates)

In [ ]:
rhs0 = rhs(0,H0_iso)

In [ ]:
print(rhs0[inf_to].max())

In [ ]:
rhs0_int = (H0_iso.T * rhs.Q_int).T

In [ ]:
print(rhs0_int[inf_possible].min())

In [ ]:
print(H0_iso[inf_possible].max())

In [ ]:
print(H0_iso[inf_possible].dot(inf_rates.T))

In [ ]:
print(inf_rates[inf_rates>0])

In [ ]:
for i in range(0,2):
    print(i)